To run this, press "*Runtime*" and press "*Run all*" on a **free** Tesla T4 Google Colab instance!
<div class="align-center">
<a href="https://unsloth.ai/"><img src="https://github.com/unslothai/unsloth/raw/main/images/unsloth%20new%20logo.png" width="115"></a>
<a href="https://discord.gg/unsloth"><img src="https://github.com/unslothai/unsloth/raw/main/images/Discord button.png" width="145"></a>
<a href="https://docs.unsloth.ai/"><img src="https://github.com/unslothai/unsloth/blob/main/images/documentation%20green%20button.png?raw=true" width="125"></a></a> Join Discord if you need help + ⭐ <i>Star us on <a href="https://github.com/unslothai/unsloth">Github</a> </i> ⭐
</div>

To install Unsloth on your own computer, follow the installation instructions on our Github page [here](https://docs.unsloth.ai/get-started/installing-+-updating).

You will learn how to do [data prep](#Data), how to [train](#Train), how to [run the model](#Inference), & [how to save it](#Save)


### News

**Read our [Gemma 3 blog](https://unsloth.ai/blog/gemma3) for what's new in Unsloth and our [Reasoning blog](https://unsloth.ai/blog/r1-reasoning) on how to train reasoning models.**

Visit our docs for all our [model uploads](https://docs.unsloth.ai/get-started/all-our-models) and [notebooks](https://docs.unsloth.ai/get-started/unsloth-notebooks).


### Installation

In [1]:
%%capture
import os
if "COLAB_" not in "".join(os.environ.keys()):
    !pip install unsloth vllm
else:
    # [NOTE] Do the below ONLY in Colab! Use [[pip install unsloth vllm]]
    !pip install --no-deps unsloth vllm

In [ ]:
#@title Colab Extra Install { display-mode: "form" }
%%capture
import os
if "COLAB_" not in "".join(os.environ.keys()):
    !pip install unsloth vllm
else:
    !pip install --no-deps unsloth vllm
    # [NOTE] Do the below ONLY in Colab! Use [[pip install unsloth vllm]]
    # Skip restarting message in Colab
    import sys, re, requests; modules = list(sys.modules.keys())
    for x in modules: sys.modules.pop(x) if "PIL" in x or "google" in x else None
    !pip install --no-deps bitsandbytes accelerate xformers==0.0.29.post3 peft "trl==0.15.2" triton cut_cross_entropy unsloth_zoo
    !pip install sentencepiece protobuf datasets huggingface_hub hf_transfer

    # vLLM requirements - vLLM breaks Colab due to reinstalling numpy
    f = requests.get("https://raw.githubusercontent.com/vllm-project/vllm/refs/heads/main/requirements/common.txt").content
    with open("vllm_requirements.txt", "wb") as file:
        file.write(re.sub(rb"(transformers|numpy|xformers)[^\n]{1,}\n", b"", f))
    !pip install -r vllm_requirements.txt

In [2]:
!pip3 uninstall numpy
!pip3 install numpy==1.24.4

Found existing installation: numpy 2.2.5
Uninstalling numpy-2.2.5:
  Would remove:
    /home/ubuntu/.local/bin/f2py
    /home/ubuntu/.local/bin/numpy-config
    /home/ubuntu/.local/lib/python3.10/site-packages/numpy-2.2.5.dist-info/*
    /home/ubuntu/.local/lib/python3.10/site-packages/numpy.libs/libgfortran-040039e1-0352e75f.so.5.0.0
    /home/ubuntu/.local/lib/python3.10/site-packages/numpy.libs/libquadmath-96973f99-934c22de.so.0.0.0
    /home/ubuntu/.local/lib/python3.10/site-packages/numpy.libs/libscipy_openblas64_-6bb31eeb.so
    /home/ubuntu/.local/lib/python3.10/site-packages/numpy/*
Proceed (Y/n)? ^C
ERROR: Operation cancelled by user
Defaulting to user installation because normal site-packages is not writeable
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.3/17.3 MB 169.0 MB/s eta 0:00:00
  Attempting uninstall: numpy
    Found existing installation: numpy 2.2.5
    Uninstalling numpy-2.2.5:
      Successfully uninstalled numpy-2.2.5
  Consider adding this directory to PATH or

In [22]:
!pip uninstall unsloth -y && pip install --upgrade --no-cache-dir --no-deps git+https://github.com/unslothai/unsloth.git

Found existing installation: unsloth 2025.3.19
Uninstalling unsloth-2025.3.19:
  Successfully uninstalled unsloth-2025.3.19
Defaulting to user installation because normal site-packages is not writeable
  Cloning https://github.com/unslothai/unsloth.git to /tmp/pip-req-build-5si0v1r2
  Running command git clone --filter=blob:none --quiet https://github.com/unslothai/unsloth.git /tmp/pip-req-build-5si0v1r2
  Resolved https://github.com/unslothai/unsloth.git to commit 6c234d5a66adb76b9b93fb0f2445648199d88e66
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for unsloth: filename=unsloth-2025.3.19-py3-none-any.whl size=192660 sha256=c443dcc4e023426fa128b8c4b81347c1e67b535694f8cfc74bd78779bae32141
  Stored in directory: /tmp/pip-ephem-wheel-cache-tptvre_t/wheels/ed/d4/e9/76fb290ee3df0a5fc21ce5c2c788e29e9607a2353d8342fd0d
Successfully built unsloth


In [2]:
!pip uninstall vllm

Found existing installation: vllm 0.8.4
Uninstalling vllm-0.8.4:
  Would remove:
    /home/ubuntu/.local/bin/vllm
    /home/ubuntu/.local/lib/python3.10/site-packages/vllm-0.8.4.dist-info/*
    /home/ubuntu/.local/lib/python3.10/site-packages/vllm/*
Proceed (Y/n)? ^C
ERROR: Operation cancelled by user


[rank0]:[W420 08:17:52.100938014 ProcessGroupNCCL.cpp:1496] Warning: WARNING: destroy_process_group() was not called before program exit, which can leak resources. For more info, please see https://pytorch.org/docs/stable/distributed.html#shutdown (function operator())


In [2]:
import gc, torch
gc.collect()
torch.cuda.empty_cache()

### Unsloth

Load up `Llama 3.1 8B Instruct`, and set parameters

In [1]:
from unsloth import FastLanguageModel
import torch
max_seq_length = 4096 # Can increase for longer reasoning traces
# max_seq_length = 2048 # Can increase for longer reasoning traces
lora_rank = 8 # Larger rank = smarter, but slower

model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = "unsloth/DeepSeek-R1-Distill-Qwen-7B",
    # model_name = "unsloth/DeepSeek-R1-Distill-Llama-8B",
    # model_name = "unsloth/Llama-3.2-1B-Instruct",
    fix_tokenizer    = False,           # <— let it use the HF tokenizer directly
    max_seq_length = max_seq_length,
    load_in_4bit = False, # False for LoRA 16bit
    fast_inference = True, # Enable vLLM fast inference
    max_lora_rank = lora_rank,
    gpu_memory_utilization = 0.6, # Reduce if out of memory
)


🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.
Unsloth: Failed to patch Gemma3ForConditionalGeneration.
🦥 Unsloth Zoo will now patch everything to make training faster!
INFO 04-21 04:21:15 __init__.py:207] Automatically detected platform cuda.
==((====))==  Unsloth 2025.3.19: Fast Qwen2 patching. Transformers: 4.51.3. vLLM: 0.7.3.
   \\   /|    NVIDIA L40S. Num GPUs = 1. Max memory: 44.309 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.5.1+cu124. CUDA: 8.9. CUDA Toolkit: 12.4. Triton: 3.1.0
\        /    Bfloat16 = TRUE. FA [Xformers = 0.0.28.post3. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!
Unsloth: vLLM loading unsloth/DeepSeek-R1-Distill-Qwen-7B with actual GPU utilization = 59.38%
Unsloth: Your GPU has CUDA compute capability 8.9 with VRAM = 44.31 GB.
Unsloth: Using conservativeness = 1.0. Chunked prefill tokens = 4096. Num Sequences = 256.


[W421 04:21:23.798132074 CUDAAllocatorConfig.h:28] Warning: expandable_segments not supported on this platform (function operator())


INFO 04-21 04:21:24 weight_utils.py:254] Using model weights format ['*.safetensors']


Loading safetensors checkpoint shards:   0% Completed | 0/4 [00:00<?, ?it/s]


INFO 04-21 04:21:26 model_runner.py:1115] Loading model weights took 14.3854 GB
INFO 04-21 04:21:26 punica_selector.py:18] Using PunicaWrapperGPU.
INFO 04-21 04:21:28 worker.py:267] Memory profiling takes 1.34 seconds
INFO 04-21 04:21:28 worker.py:267] the current vLLM instance can use total_gpu_memory (44.31GiB) x gpu_memory_utilization (0.59) = 26.31GiB
INFO 04-21 04:21:28 worker.py:267] model weights take 14.39GiB; non_torch_memory takes 0.08GiB; PyTorch activation peak memory takes 1.43GiB; the rest of the memory reserved for KV Cache is 10.41GiB.
INFO 04-21 04:21:28 executor_base.py:111] # cuda blocks: 12184, # CPU blocks: 5851
INFO 04-21 04:21:28 executor_base.py:116] Maximum concurrency for 4096 tokens per request: 47.59x
INFO 04-21 04:21:32 model_runner.py:1434] Capturing cudagraphs for decoding. This may lead to unexpected consequences if the model is not static. To run the model in eager mode, set 'enforce_eager=True' or use '--enforce-eager' in the CLI. If out-of-memory erro

Capturing CUDA graph shapes: 100%|██████████| 35/35 [00:24<00:00,  1.41it/s]

INFO 04-21 04:21:57 model_runner.py:1562] Graph capturing finished in 25 secs, took 0.33 GiB
INFO 04-21 04:21:57 llm_engine.py:436] init engine (profile, create kv cache, warmup model) took 31.14 seconds


In [2]:

model = FastLanguageModel.get_peft_model(
    model,
    r = lora_rank, # Choose any number > 0 ! Suggested 8, 16, 32, 64, 128
    target_modules = [
        "q_proj", "k_proj", "v_proj", "o_proj",
        "gate_proj", "up_proj", "down_proj",
    ], # Remove QKVO if out of memory
    lora_alpha = lora_rank,
    use_gradient_checkpointing = "unsloth", # Enable long context finetuning
    random_state = 3407,
)

Unsloth 2025.3.19 patched 28 layers with 28 QKV layers, 28 O layers and 28 MLP layers.


### Data Prep
<a name="Data"></a>

We directly leverage [@willccbb](https://gist.github.com/willccbb/4676755236bb08cab5f4e54a0475d6fb) for data prep and all reward functions. You are free to create your own!

In [3]:
import re
from datasets import load_dataset, Dataset

In [4]:
from huggingface_hub import login

import wandb

wandb.login(key="<key>")

login(token="<key>")

wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.
wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /home/ubuntu/.netrc
wandb: Currently logged in as: yufa to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


In [5]:
dataset = load_dataset("MasterZhou/econ_reasoning")['train']

In [6]:
print(dataset[0]["prompt"])

[{'content': 'You are given a reasoning problem in Economics. Please reason step by step to solve it.\n\nEnclose your reasoning in <think> and </think>. Then, give your final answer using the format \\boxed{Option X: full choice text}.\n\nYou must include both the option number and the full text of your chosen answer.\n\nQuestion:\nTwo firms, A and B, are involved in a reciprocal servicing agreement over an indefinite horizon. Each period, if both firms fulfill their servicing obligations, each receives a benefit of $16858.48. However, if one firm renegs on the agreement while the other firm fulfills their obligation, the reneging firm receives a benefit of $36498.39, while the dutiful firm incurs a cost of $79329.61. If both firms decide to renege on their obligations, they each receive $31218.06. Given the discount factor is 0.41, which of the following outcomes is enforceable in a Nash equilibrium?\n\nOptions:\nOption 1: Both firms A and B fulfill their servicing obligations every p

In [7]:
# 2) define the mapper to append " <think>" to each content
def append_think_to_content(example):
    new_prompts = []
    for p in example["prompt"]:
        p = p.copy()  # avoid mutating the original example
        if "content" in p:
            p["content"] = p["content"] + "\n<think>"
        new_prompts.append(p)
    return {"prompt": new_prompts}

# 3) apply it
dataset = dataset.map(append_think_to_content)

In [8]:
# 4) print a couple of examples to verify
for i in range(2):
    print(f"Example {i}:")
    for p in dataset[i]["prompt"]:
        print("  content:", p["content"])
        print("  role:   ", p.get("role"))
    print("answer:", dataset[i]["answer"])
    print()

Example 0:
  content: You are given a reasoning problem in Economics. Please reason step by step to solve it.

Enclose your reasoning in <think> and </think>. Then, give your final answer using the format \boxed{Option X: full choice text}.

You must include both the option number and the full text of your chosen answer.

Question:
Two firms, A and B, are involved in a reciprocal servicing agreement over an indefinite horizon. Each period, if both firms fulfill their servicing obligations, each receives a benefit of $16858.48. However, if one firm renegs on the agreement while the other firm fulfills their obligation, the reneging firm receives a benefit of $36498.39, while the dutiful firm incurs a cost of $79329.61. If both firms decide to renege on their obligations, they each receive $31218.06. Given the discount factor is 0.41, which of the following outcomes is enforceable in a Nash equilibrium?

Options:
Option 1: Both firms A and B fulfill their servicing obligations every peri

In [9]:
import re
# ====================================================================== #
# 1.  CONSTANTS & REGEXES                                                #
# ====================================================================== #
BOXED_RE  = re.compile(r"\\boxed\{(.*?)\}")
OPTION_RE = re.compile(r"Option\s+([0-9]+)", re.I)

FORMAT_PENALTY = -2.0    # Stage‑A fail
PARSE_PENALTY  = -3.0    # Stage‑B fail
CORRECT_BOX    = +3.0    # Stage‑C success, boxed
PARTIAL        =  0.0    # Stage‑C success, unboxed
WRONG          = -3.0    # Stage‑C wrong answer

In [10]:
# =================================================================== #
# 2.  FORMAT CHECK  (Stage‑A)                                          #
# =================================================================== #
def format_score(text: str) -> float:
    """
    Minimal contract:

      • exactly one </think>
      • if a \\boxed{…} exists, its *first* occurrence is after </think>

    +0.5  correct </think> count
    +0.25 order OK  (*or* no box at all)
    ---------------------------------
    −1    per violated rule
    """
    score = 0.0

    # 1) </think> count
    score += 0.5 if text.count("</think>") == 1 else -1.0

    # 2) ordering (only if count is correct)
    try:
        think_end = text.index("</think>")
        first_box = BOXED_RE.search(text)
        if first_box and first_box.start() < think_end:
            score -= 1.0                       # box appears before </think>
        else:
            score += 0.25                      # either no box or order OK
    except ValueError:
        score -= 1.0                           # shouldn’t happen, tag missing

    return round(score, 2)   # >0 → passes Stage‑A

# =================================================================== #
# 3.  ANSWER EXTRACTION  (Stage‑B)   — AFTER </think> ONLY            #
# =================================================================== #
def _tail_after_think(text: str) -> str:
    """
    Return the substring that starts *immediately after* the one and only
    </think> tag.  (Stage‑A guarantees that tag exists exactly once.)
    """
    end = text.index("</think>") + len("</think>")
    return text[end:]


def extract_boxed(text: str) -> str:
    """
    Find the first \\boxed{…} *after* </think>; return its inner text, or ''.
    """
    tail = _tail_after_think(text)
    m = BOXED_RE.search(tail)
    return m.group(1).strip() if m else ""


def extract_unboxed(text: str) -> str:
    """
    Look for the first 'Option X' label *after* </think>.  Return
    'Option X' if found, otherwise '' (no fallback to earlier text).
    """
    tail = _tail_after_think(text)
    m = OPTION_RE.search(tail)
    return f"Option {m.group(1)}" if m else ""

def same_option(gold: str, pred: str) -> bool:
    """Does gold and pred contain the same option number?"""
    g = OPTION_RE.search(gold)
    p = OPTION_RE.search(pred)
    return g and p and g.group(1) == p.group(1)

# =================================================================== #
# 4.  HIERARCHICAL REWARD FUNCTION  (with debug)                       #
# =================================================================== #
def hierarchical_reward(prompts, completions, answer, **kw):
    """
    Stage‑A : structure check via format_score
    Stage‑B : extract first boxed (or unboxed fallback)
    Stage‑C : grade correctness
    """
    gold = answer[0].strip()
    rewards = []

    for comp in completions:
        resp = comp[0]["content"]

        # -------- A. structure gate ----------------------------------
        if format_score(resp) <= 0:
            reward = FORMAT_PENALTY
            boxed = unboxed = parsed = ""
            rewards.append(reward)

        else:
            # -------- B. parse gate ----------------------------------
            boxed   = extract_boxed(resp)
            unboxed = "" if boxed else extract_unboxed(resp)
            parsed  = boxed or unboxed

            if not parsed:
                reward = PARSE_PENALTY
                rewards.append(reward)
            else:
                # -------- C. correctness -----------------------------
                if parsed == gold:
                    reward = CORRECT_BOX        # exact match (boxed or fallback)
                elif same_option(gold, parsed):
                    reward = PARTIAL            # only option number matches
                else:
                    reward = WRONG
                rewards.append(reward)

        # -------- debug output --------------------------------------
        print("-" * 40)
        print(f"Question:\n{prompts[0][-1]['content']}\n")
        print(f"Target   : {gold}")
        print(f"Response :\n{resp}\n")
        print(f"Extracted boxed   : {boxed or '—'}")
        print(f"Extracted unboxed : {unboxed or '—'}")
        print(f"Final parsed ans. : {parsed or '—'}")
        print(f"Reward   : {reward}")

    return rewards

In [11]:
# import re

# # ---------- 1. helpers --------------------------------------------------------
# BOXED_RE   = re.compile(r"\\boxed\{(.*?)\}")
# OPTION_RE  = re.compile(r"Option\s+([0-9]+)", re.IGNORECASE)  # fallback parser



# def extract_unboxed_answer(text: str) -> str:
#     """
#     Fallback: try to pull the answer from inside <answer> when no \\boxed{…}
#     is present.  Here we simply capture the first 'Option X' we see, but you
#     can adapt the logic to your exact label format.
#     """
#     block = _get_answer_block(text)
#     # Example formats we try to recognise
#     opt_match = OPTION_RE.search(block)
#     if opt_match:
#         return f"Option {opt_match.group(1)}"
#     return block.strip()  # last resort – raw text


# # ---------- 2. reward function ------------------------------------------------
# def correctness_reward_func(prompts, completions, answer, **kwargs) -> list[float]:
#     """
#     Reward logic:
#       ① If <answer> contains \\boxed{…}: compare →  +3 / –3
#       ② Else if <answer> contains an unboxed answer: +1 / –3
#       ③ Else (no answer found):                    –3
#     """
#     gt = answer[0].strip()                # the gold‑truth answer once
#     raw_responses = [c[0]["content"] for c in completions]
#     rewards = []

#     for resp in raw_responses:
#         ans_block = _get_answer_block(resp)
#         boxed     = extract_boxed_answer_from_xml(resp)

#         if boxed:                        # ① boxed case
#             reward = 3.0 if boxed == gt else -3.0
#         elif ans_block:                  # ② unboxed but something there
#             unboxed = extract_unboxed_answer(resp)
#             reward  = 1.0 if unboxed == gt else -3.0
#         else:                            # ③ nothing at all
#             reward = -3.0

#         rewards.append(reward)

#         # ---- optional debug printout ---------------------------------------
#         print("-" * 40)
#         print(f"Question:\n{prompts[0][-1]['content']}\n")
#         print(f"Target  : {gt}")
#         print(f"Response:\n{resp}\n")
#         print(f"Boxed   : {boxed if boxed else '—'}")
#         print(f"Unboxed : {unboxed if not boxed else '—'}")
#         print(f"Reward  : {reward}")
#     # ------------------------------------------------------------------------

#     return rewards

# def format_score(text: str) -> float:
#     score = 0.0
#     score += 0.5 if text.count("</think>") == 1 else -1
#     # give score for having </think> before <answer> and </answer>.
#     # give score for having <answer> before </answer>.
#     score += 0.25 if text.count("<answer>") == 1 and text.count("</answer>") == 1 else -0.5

#     # answer contains box or not
#     answer_block = text.split("<answer>")[-1].split("</answer>")[0]
#     if re.search(r"\\boxed\{(.*?)\}", answer_block):
#         score += 0.05
#     else:
#         score -= 0.5

#     return round(score, 2)

# def format_reward_func(completions, **kwargs) -> list[float]:
#     return [format_score(c[0]["content"]) for c in completions]

In [12]:
# import re

# def extract_boxed_answer_from_xml(text: str) -> str:
#     """Extracts the boxed final answer from the <answer> tag."""
#     try:
#         answer_block = text.split("<answer>")[-1].split("</answer>")[0]
#         match = re.search(r"\\boxed\{(.*?)\}", answer_block)
#         return match.group(1).strip() if match else ""
#     except Exception:
#         return ""

# def correctness_reward_func(prompts, completions, answer, **kwargs) -> list[float]:
#     responses = [completion[0]['content'] for completion in completions]
#     extracted_responses = [extract_boxed_answer_from_xml(r) for r in responses]
#     print('-'*30)
#     print(f"Question:\n{prompts[0][-1]['content']}")
#     print(f"Target Answer:\n{answer[0]}")
#     print(f"Model Response:\n{responses[0]}")
#     print(f"Extracted Answer:\n{extracted_responses[0]}")

#     return [3.0 if r == answer[0] else -3.0 for r in extracted_responses]


# def strict_format_reward_func(completions, **kwargs) -> list[float]:
#     pattern = r"^<think>\n.*?\n</think>\n<answer>\n.*?\\boxed\{.*?\}.*?\n?</answer>\s*\Z"
#     responses = [completion[0]["content"] for completion in completions]
#     return [0.5 if re.match(pattern, r, flags=re.DOTALL) else -0.5 for r in responses]


# def soft_format_reward_func(completions, **kwargs) -> list[float]:
#     pattern = r"<think>.*?</think>\s*<answer>.*?\\boxed\{.*?\}.*?</answer>"

#     responses = [completion[0]["content"] for completion in completions]
#     return [0.5 if re.search(pattern, r, flags=re.DOTALL) else -0.5 for r in responses]

# def count_tags_score(text: str) -> float:
#     score = 0.0
#     score += 0.25 if text.count("<think>") == 1 and text.count("</think>") == 1 else 0
#     score += 0.25 if text.count("<answer>") == 1 and text.count("</answer>") == 1 else 0

#     # \boxed{} correctness
#     boxed = re.findall(r"\\boxed\{(.*?)\}", text)
#     if len(boxed) == 1:
#         score += 0.25
#     else:
#         score -= 0.25

#     # Positioning: make sure boxed is *inside* <answer>
#     answer_block = text.split("<answer>")[-1].split("</answer>")[0]
#     if re.search(r"\\boxed\{(.*?)\}", answer_block):
#         score += 0.25
#     else:
#         score -= 0.25

#     return round(score, 2)

# def tagcount_reward_func(completions, **kwargs) -> list[float]:
#     return [count_tags_score(c[0]["content"]) for c in completions]


In [13]:
tests = [
    # 1) Perfect boxed after </think>
    {
        "desc": "boxed correct after think",
        "text": "<think>...reason...</think> \\boxed{Option 1: A}",
        "gold": "Option 1: A",
        "expected": +3.0
    },
    # 2) Perfect unboxed after </think>
    {
        "desc": "unboxed correct after think",
        "text": "<think>logic</think> Option 1: A",
        "gold": "Option 1: A",
        "expected": +1.0
    },
    # 3) Wrong boxed after </think>
    {
        "desc": "boxed wrong after think",
        "text": "<think>…</think> \\boxed{Option 2: B}",
        "gold": "Option 1: A",
        "expected": -3.0
    },
    # 4) Wrong unboxed after </think>
    {
        "desc": "unboxed wrong after think",
        "text": "<think>…</think> Option 2: B",
        "gold": "Option 1: A",
        "expected": -3.0
    },
    # 5) Partial: correct option-number unboxed
    {
        "desc": "partial unboxed after think",
        "text": "<think>…</think> Option 1: WRONG TEXT",
        "gold": "Option 1: A",
        "expected": +1.0
    },
    # 6) Box before </think> only, unboxed correct after
    {
        "desc": "box before think, unboxed after",
        "text": "\\boxed{Option 1: A}<think>…</think> Option 1: A",
        "gold": "Option 1: A",
        "expected": +1.0
    },
    # 7) Box before </think> only, no content after
    {
        "desc": "box before think only",
        "text": "\\boxed{Option 1: A}<think>…</think>",
        "gold": "Option 1: A",
        "expected": -3.0    # parse‑fail
    },
    # 8) No </think> tag
    {
        "desc": "missing </think>",
        "text": "<think>oops<answer></answer> \\boxed{Option 1: A}",
        "gold": "Option 1: A",
        "expected": -2.0   # format‑fail
    },
    # 9) Multiple boxes after </think> (first wrong, second correct)
    {
        "desc": "multiple boxes, first wrong",
        "text": "<think>…</think> \\boxed{Option 2: B} then \\boxed{Option 1: A}",
        "gold": "Option 1: A",
        "expected": -3.0   # picks first box → wrong
    },
    # 10) Box appears *before* </think>
    {
        "desc": "box before think wrong order",
        "text": "\\boxed{Option 1: A}</think> rest",
        "gold": "Option 1: A",
        "expected": -2.0   # format‑fail
    },
    # 11) Unboxed option appears *before* </think> only
    {
        "desc": "unboxed before think only",
        "text": "Option 1: A<think>…</think>",
        "gold": "Option 1: A",
        "expected": -3.0   # no parse after </think`
    },
    # 12) No box or option at all
    {
        "desc": "no answer after think",
        "text": "<think>…</think> I don’t know",
        "gold": "Option 1: A",
        "expected": -3.0   # parse‑fail
    },
]

# ---------------------------------------------------- #
# Run them                                           #
# ---------------------------------------------------- #
for case in tests:
    prompts     = [[{"role":"user","content":"Q"}]]
    completions = [[{"content": case["text"]}]]
    answer      = [case["gold"]]
    reward = hierarchical_reward(prompts, completions, answer)[0]
    print(f"{case['desc']:<30} → got {reward:+4} (expected {case['expected']:+4})")


----------------------------------------
Question:
Q

Target   : Option 1: A
Response :
<think>...reason...</think> \boxed{Option 1: A}

Extracted boxed   : Option 1: A
Extracted unboxed : —
Final parsed ans. : Option 1: A
Reward   : 3.0
boxed correct after think      → got +3.0 (expected +3.0)
----------------------------------------
Question:
Q

Target   : Option 1: A
Response :
<think>logic</think> Option 1: A

Extracted boxed   : —
Extracted unboxed : Option 1
Final parsed ans. : Option 1
Reward   : 0.0
unboxed correct after think    → got +0.0 (expected +1.0)
----------------------------------------
Question:
Q

Target   : Option 1: A
Response :
<think>…</think> \boxed{Option 2: B}

Extracted boxed   : Option 2: B
Extracted unboxed : —
Final parsed ans. : Option 2: B
Reward   : -3.0
boxed wrong after think        → got -3.0 (expected -3.0)
----------------------------------------
Question:
Q

Target   : Option 1: A
Response :
<think>…</think> Option 2: B

Extracted boxed   : —
Ext

<a name="Train"></a>
### Train the model

Now set up GRPO Trainer and all configurations!

In [14]:
max_prompt_length = 512
# max_prompt_length = 1024

from trl import GRPOConfig, GRPOTrainer
training_args = GRPOConfig(
    learning_rate = 5e-6,
    adam_beta1 = 0.9,
    adam_beta2 = 0.99,
    weight_decay = 0.1,
    warmup_ratio = 0.1,
    lr_scheduler_type = "cosine",
    optim = "paged_adamw_8bit",
    logging_steps = 1,
    per_device_train_batch_size = 8,
    gradient_accumulation_steps = 4, # Increase to 4 for smoother training
    num_generations = 6, # Decrease if out of memory
    max_prompt_length = max_prompt_length,
    max_completion_length = max_seq_length - max_prompt_length,
    # num_train_epochs = 3, # Set to 1 for a full training run
    max_steps = 350,
    save_steps = 25,
    max_grad_norm = 0.1,
    report_to = "wandb", # Can use Weights & Biases
    output_dir = "outputs",
)

Unsloth: We now expect `per_device_train_batch_size` to be a multiple of `num_generations`.
We will change the batch size of 8 to the `num_generations` of 6


And let's run the trainer! If you scroll up, you'll see a table of rewards. The goal is to see the `reward` column increase!

You might have to wait 150 to 200 steps for any action. You'll probably get 0 reward for the first 100 steps. Please be patient!

| Step | Training Loss | reward    | reward_std | completion_length | kl       |
|------|---------------|-----------|------------|-------------------|----------|
| 1    | 0.000000      | 0.125000  | 0.000000   | 200.000000        | 0.000000 |
| 2    | 0.000000      | 0.072375  | 0.248112   | 200.000000        | 0.000000 |
| 3    | 0.000000      | -0.079000 | 0.163776   | 182.500000        | 0.000005 |


In [15]:
tokenizer.chat_template = \
"{% for message in messages %}{{ message['content'] }} {% endfor %}"


In [19]:
import torch

_original_load = torch.load
def _unsafe_load(*args, **kwargs):
    kwargs["weights_only"] = False      # override whatever the caller passes
    return _original_load(*args, **kwargs)

torch.load = _unsafe_load              # patch in

# ───── build trainer as before ───────────────────────────────────────
trainer = GRPOTrainer(
    model            = model,
    processing_class = tokenizer,
    reward_funcs     = [hierarchical_reward],
    args             = training_args,
    train_dataset    = dataset,
)

checkpoint = "outputs/checkpoint-100"
with open("training.log", "w") as out, open("training.err","w") as err:
    with redirect_stdout(out), redirect_stderr(err):
        trainer.train(resume_from_checkpoint=checkpoint)


==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 2,100 | Num Epochs = 1 | Total steps = 350
O^O/ \_/ \    Batch size per device = 6 | Gradient accumulation steps = 4
\        /    Data Parallel GPUs = 1 | Total batch size (6 x 4 x 1) = 24
 "-____-"     Trainable parameters = 20,185,088/7,635,801,600 (0.26% trained)


KeyboardInterrupt: 

In [20]:
model.push_to_hub("MasterZhou/recon")
tokenizer.push_to_hub("MasterZhou/recon")

README.md:   0%|          | 0.00/78.0 [00:00<?, ?B/s]

  0%|          | 0/1 [00:00<?, ?it/s]

adapter_model.safetensors:   0%|          | 0.00/80.8M [00:00<?, ?B/s]

Saved model to https://huggingface.co/MasterZhou/recon


  0%|          | 0/1 [00:00<?, ?it/s]

tokenizer.json:   0%|          | 0.00/11.4M [00:00<?, ?B/s]

In [21]:
model.save_lora("recon_grpo_saved_lora")

<a name="Inference"></a>
### Inference
Now let's try the model we just trained! First, let's first try the model without any GRPO trained:

In [1]:
import os
import pandas as pd
import re
from openai import OpenAI
import json
import time

In [2]:
OPENAI_API_KEY = "<key>"
NVIDIA_API_KEY = "<key>"
DATA_PATH = "distilled_df.pkl"
RESULT_PATH = 'results_ds_7b_tuned_0421'
model = "deepseek-ai/deepseek-r1-distill-qwen-7b"

In [3]:
distilled_df = pd.read_pickle(DATA_PATH)

In [4]:
from huggingface_hub import login

login(token="<key>")

In [5]:
from transformers import AutoModelForCausalLM, AutoTokenizer
from peft import PeftModel
import torch
import re

# 1) Load base model + tokenizer
base_name = "unsloth/DeepSeek-R1-Distill-Qwen-7B"
tokenizer = AutoTokenizer.from_pretrained(base_name, trust_remote_code=True)
base = AutoModelForCausalLM.from_pretrained(
    base_name,
    trust_remote_code=True,
    device_map="auto",
    torch_dtype=torch.bfloat16,
)

# 2) Wrap with your LoRA adapter on Hugging Face Hub or local dir
#    If you pushed to "MasterZhou/recon":
model = PeftModel.from_pretrained(base, "MasterZhou/recon")
model.eval()

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

adapter_config.json:   0%|          | 0.00/863 [00:00<?, ?B/s]

adapter_model.safetensors:   0%|          | 0.00/80.8M [00:00<?, ?B/s]

PeftModelForCausalLM(
  (base_model): LoraModel(
    (model): Qwen2ForCausalLM(
      (model): Qwen2Model(
        (embed_tokens): Embedding(152064, 3584, padding_idx=151654)
        (layers): ModuleList(
          (0-27): 28 x Qwen2DecoderLayer(
            (self_attn): Qwen2Attention(
              (q_proj): lora.Linear(
                (base_layer): Linear(in_features=3584, out_features=3584, bias=True)
                (lora_dropout): ModuleDict(
                  (default): Identity()
                )
                (lora_A): ModuleDict(
                  (default): Linear(in_features=3584, out_features=8, bias=False)
                )
                (lora_B): ModuleDict(
                  (default): Linear(in_features=8, out_features=3584, bias=False)
                )
                (lora_embedding_A): ParameterDict()
                (lora_embedding_B): ParameterDict()
                (lora_magnitude_vector): ModuleDict()
              )
              (k_proj): lora.Linear(
 

In [6]:
# 3) Inference function
def process_question_hf(row):
    # 1) build the prompt
    prompt = (
        f"Question: {row['question']}\n"
        f"Options: {row['options']}\n\n"
        "Choose the correct option and explain your reasoning. "
        "Please reason step by step, and put your final answer within \\boxed{}.\n"
        "<think>\n"
    )

    # 2) model generate
    inputs = tokenizer(prompt, return_tensors="pt").to(model.device)
    outputs = model.generate(
        **inputs,
        max_new_tokens=4096,
        temperature=0.6,
    )
    raw = tokenizer.decode(outputs[0], skip_special_tokens=True)

    print(raw)

    # 3) split out chain-of-thought vs final
    if "</think>" in raw:
        cot, tail = raw.split("</think>", 1)
    else:
        cot, tail = "", raw

    chain_of_thought = cot.strip()
    final_answer     = tail.strip()

    # 4) extract boxed content
    m = re.search(r"\\boxed\{(.*?)\}", final_answer)
    correct_response = m.group(1).strip() if m else None

    # 5) assemble results matching your original schema
    return {
        'question_id':       row['question_id'],
        'question':          row['question'],
        'options':           row['options'],
        'expected_answer':   row.get('expected_answer'),
        'q_type':            row.get('q_type'),
        'chain_of_thought':  chain_of_thought,
        'final_answer':      final_answer,
        'correct_response':  correct_response,
    }

In [8]:
TARGET = 10

for q_type, group in distilled_df.groupby('q_type'):
    # keep only rows with an expected answer
    valid = group[group['expected_answer'].notna()]

    # randomly pick up to TARGET of them
    if len(valid) >= TARGET:
        sampled = valid.sample(n=TARGET, random_state=42)
    else:
        sampled = valid.copy()  # fewer than TARGET available

    print(f'Processing {q_type}: sampling {len(sampled)} of {len(valid)} valid rows')

    responses = []
    for _, row in sampled.iterrows():
        result = process_question_hf(row)
        if result is not None:
            responses.append(result)

    print(f'Collected {len(responses)} valid responses for q_type: {q_type}')

    # write out immediately
    df_out  = pd.DataFrame(responses)
    csv_path = os.path.join(RESULT_PATH, f"{q_type}_responses.csv")
    df_out.to_csv(csv_path, index=False)
    print(f"Saved CSV for {q_type} to {csv_path}")

Processing add_sub: sampling 10 of 240 valid rows
Question: You got your paycheck yesterday and spent some of it on clothes and need to calculate how much money you have left. What is $63 - $36
Options: Option 1: 27.0
Option 2: 41.0
Option 3: 41.0

Choose the correct option and explain your reasoning. Please reason step by step, and put your final answer within \boxed{}.
<think>
Alright, so I just got my paycheck yesterday, and I spent some of it on clothes. Now, I need to figure out how much money I have left. The question is asking me to calculate $63 minus $36. Hmm, okay, let me think through this step by step.

First, I know that subtraction is the process of taking one number away from another. In this case, I have $63, and I spent $36 on clothes. So, to find out how much I have left, I need to subtract the amount I spent from the amount I originally had. That makes sense because spending money reduces the total amount you have.

Let me write this down to visualize it better: $63 

In [ ]:
text = tokenizer.apply_chat_template([
    {"role" : "user", "content" : "Calculate pi."},
], tokenize = False, add_generation_prompt = True)

from vllm import SamplingParams
sampling_params = SamplingParams(
    temperature = 0.8,
    top_p = 0.95,
    max_tokens = 1024,
)
output = model.fast_generate(
    [text],
    sampling_params = sampling_params,
    lora_request = None,
)[0].outputs[0].text

output

Processed prompts: 100%|██████████| 1/1 [00:51<00:00, 51.81s/it, est. speed input: 0.75 toks/s, output: 17.01 toks/s]


'**Calculating Pi using Python**\n\nPi (π) is a mathematical constant representing the ratio of a circle\'s circumference to its diameter. Here\'s a simple and efficient way to calculate an approximation of pi using Python.\n\n### Using the Monte Carlo Method\n\nThe Monte Carlo method is a computational algorithm that uses random sampling to approximate a value. In this case, we can use it to estimate pi by generating random points within a square and checking if they fall inside a quarter-circle inscribed within it.\n\n```python\nimport random\nimport math\n\ndef estimate_pi(num_samples):\n    """\n    Estimate the value of pi using the Monte Carlo method.\n\n    Args:\n    num_samples (int): The number of random points to generate.\n\n    Returns:\n    float: An approximation of pi.\n    """\n    points_inside_circle = 0\n\n    for _ in range(num_samples):\n        x, y = random.random(), random.random()\n        distance = x**2 + y**2\n        if distance <= 1:\n            points_i

And now with the LoRA we just trained with GRPO - we first save the LoRA first!

In [ ]:
model.save_lora("grpo_saved_lora")

Now we load the LoRA and test:

In [ ]:
text = tokenizer.apply_chat_template([
    # {"role" : "system", "content" : SYSTEM_PROMPT},
    {"role" : "user", "content" : "Calculate pi."},
], tokenize = False, add_generation_prompt = True)

from vllm import SamplingParams
sampling_params = SamplingParams(
    temperature = 0.8,
    top_p = 0.95,
    max_tokens = 1024,
)
output = model.fast_generate(
    text,
    sampling_params = sampling_params,
    lora_request = model.load_lora("grpo_saved_lora"),
)[0].outputs[0].text

output

Processed prompts: 100%|██████████| 1/1 [00:23<00:00, 23.17s/it, est. speed input: 2.63 toks/s, output: 15.80 toks/s]


'Calculating pi to a high degree of accuracy is a complex task that requires a large amount of computational power. However, I can provide you with an approximate value of pi or show you a simple method to calculate it.\n\nOne of the simplest methods to calculate pi is the Leibniz formula, which is an infinite series:\n\npi/4 = 1 - 1/3 + 1/5 - 1/7 + 1/9 - ...\n\nThis series can be used to calculate an approximation of pi.\n\n<reasoning>\npi = 4 * (1 - 1/3 + 1/5 - 1/7 + 1/9 - ...)\n</reasoning>\n\nThis is a simple, yet effective method to calculate pi. However, the more terms you use, the more accurate the result will be.\n\nTo calculate pi to a high degree of accuracy, you would need to use a computer program to perform the calculation.\n\n<answer>\n3.141592653589793 (approximately)\n</answer>\n\nFor a more accurate result, I can provide you with a Python code snippet to calculate pi:\n\n```python\nimport math\n\ndef calculate_pi(n):\n    pi = 0.0\n    for i in range(n):\n        pi +=

Our reasoning model is much better - it's not always correct, since we only trained it for an hour or so - it'll be better if we extend the sequence length and train for longer!

<a name="Save"></a>
### Saving to float16 for VLLM

We also support saving to `float16` directly. Select `merged_16bit` for float16 or `merged_4bit` for int4. We also allow `lora` adapters as a fallback. Use `push_to_hub_merged` to upload to your Hugging Face account! You can go to https://huggingface.co/settings/tokens for your personal tokens.

In [ ]:
# Merge to 16bit
if False: model.save_pretrained_merged("model", tokenizer, save_method = "merged_16bit",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "merged_16bit", token = "")

# Merge to 4bit
if False: model.save_pretrained_merged("model", tokenizer, save_method = "merged_4bit",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "merged_4bit", token = "")

# Just LoRA adapters
if False: model.save_pretrained_merged("model", tokenizer, save_method = "lora",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "lora", token = "")

### GGUF / llama.cpp Conversion
To save to `GGUF` / `llama.cpp`, we support it natively now! We clone `llama.cpp` and we default save it to `q8_0`. We allow all methods like `q4_k_m`. Use `save_pretrained_gguf` for local saving and `push_to_hub_gguf` for uploading to HF.

Some supported quant methods (full list on our [Wiki page](https://github.com/unslothai/unsloth/wiki#gguf-quantization-options)):
* `q8_0` - Fast conversion. High resource use, but generally acceptable.
* `q4_k_m` - Recommended. Uses Q6_K for half of the attention.wv and feed_forward.w2 tensors, else Q4_K.
* `q5_k_m` - Recommended. Uses Q6_K for half of the attention.wv and feed_forward.w2 tensors, else Q5_K.

[**NEW**] To finetune and auto export to Ollama, try our [Ollama notebook](https://colab.research.google.com/github/unslothai/notebooks/blob/main/nb/Llama3_(8B)-Ollama.ipynb)

In [ ]:
# Save to 8bit Q8_0
if False: model.save_pretrained_gguf("model", tokenizer,)
# Remember to go to https://huggingface.co/settings/tokens for a token!
# And change hf to your username!
if False: model.push_to_hub_gguf("hf/model", tokenizer, token = "")

# Save to 16bit GGUF
if False: model.save_pretrained_gguf("model", tokenizer, quantization_method = "f16")
if False: model.push_to_hub_gguf("hf/model", tokenizer, quantization_method = "f16", token = "")

# Save to q4_k_m GGUF
if False: model.save_pretrained_gguf("model", tokenizer, quantization_method = "q4_k_m")
if False: model.push_to_hub_gguf("hf/model", tokenizer, quantization_method = "q4_k_m", token = "")

# Save to multiple GGUF options - much faster if you want multiple!
if False:
    model.push_to_hub_gguf(
        "hf/model", # Change hf to your username!
        tokenizer,
        quantization_method = ["q4_k_m", "q8_0", "q5_k_m",],
        token = "",
    )

Now, use the `model-unsloth.gguf` file or `model-unsloth-Q4_K_M.gguf` file in llama.cpp or a UI based system like Jan or Open WebUI. You can install Jan [here](https://github.com/janhq/jan) and Open WebUI [here](https://github.com/open-webui/open-webui)

And we're done! If you have any questions on Unsloth, we have a [Discord](https://discord.gg/unsloth) channel! If you find any bugs or want to keep updated with the latest LLM stuff, or need help, join projects etc, feel free to join our Discord!

Some other links:
1. Train your own reasoning model - Llama GRPO notebook [Free Colab](https://colab.research.google.com/github/unslothai/notebooks/blob/main/nb/Llama3.1_(8B)-GRPO.ipynb)
2. Saving finetunes to Ollama. [Free notebook](https://colab.research.google.com/github/unslothai/notebooks/blob/main/nb/Llama3_(8B)-Ollama.ipynb)
3. Llama 3.2 Vision finetuning - Radiography use case. [Free Colab](https://colab.research.google.com/github/unslothai/notebooks/blob/main/nb/Llama3.2_(11B)-Vision.ipynb)
6. See notebooks for DPO, ORPO, Continued pretraining, conversational finetuning and more on our [documentation](https://docs.unsloth.ai/get-started/unsloth-notebooks)!

<div class="align-center">
  <a href="https://unsloth.ai"><img src="https://github.com/unslothai/unsloth/raw/main/images/unsloth%20new%20logo.png" width="115"></a>
  <a href="https://discord.gg/unsloth"><img src="https://github.com/unslothai/unsloth/raw/main/images/Discord.png" width="145"></a>
  <a href="https://docs.unsloth.ai/"><img src="https://github.com/unslothai/unsloth/blob/main/images/documentation%20green%20button.png?raw=true" width="125"></a>

  Join Discord if you need help + ⭐️ <i>Star us on <a href="https://github.com/unslothai/unsloth">Github</a> </i> ⭐️
</div>
